In [ ]:
# residual noise from SML
# 1. smooth Temperature at 100cm until noise is gone
# apply same smoothing factor to SML
# -> which noise is driven by atmospheric drivers?

# Pia Goecke, pia.goecke@uni-oldenburg.de
# 26.11.2024

In [1]:
from pathlib import Path
import matplotlib.pyplot as plt
import seaborn as sns
from glob import glob
import pandas as pd
import matplotlib.animation as animation
import numpy as np
from scipy.interpolate import griddata
import warnings
warnings.filterwarnings("ignore")
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
import numpy as np
import os
import matplotlib.dates as mdates
import matplotlib as mpl
import re
from itertools import chain
import matplotlib
import matplotlib.ticker as ticker
import scipy.io
from statsmodels.nonparametric.smoothers_lowess import lowess
import gsw
from scipy.stats import pearsonr
from matplotlib.pyplot import cm
from cartopy import config
import cartopy.crs as ccrs
from mpl_toolkits.axes_grid1 import make_axes_locatable
import matplotx
from cycler import cycler
from matplotlib.dates import date2num
import cartopy.feature as cfeature  #adding features in the map
#import gpxpy
import xml.etree.ElementTree as ET
import plotly.graph_objs as go

In [2]:
#read data and rename cols
os.chdir('C:/Users/piago/Documents/Uni/5_Semester/Hiwi')
csv_file = "C:/Users/piago/Documents/Uni/5_Semester/Hiwi/Data/HE614_All_Grids_Single_Sheet.xlsx"

# Read the Excel file
df = pd.read_excel(csv_file, skiprows=10)
df = df.set_index('Date_Time')
df.index = pd.to_datetime(df.index)
df.rename(columns={'CTD_Temperature_SML' : 'CTD_Temp_SML',
                   'CTD_Temperature_30cm' : 'CTD_Temperature_30cm_[°C]',
                   'CTD_Temperature_40cm' : 'CTD_Temperature_40cm_[°C]',
                   'CTD_Temperature_50cm_[°C]' : 'CTD_Temperature_50',
                   'CTD_Temperature_60cm_[°C]': 'CTD_Temperature_60',
                   'CTD_Temperature_85cm' : 'CTD_Temperature_85cm_[°C]',
                   'CTD_Temperature_100cm' : 'CTD_Temperature_100cm_[°C]'}, inplace= True)

df['Date'] = df.index.date

In [3]:
# extract dfs
df_2 = df.loc['2023-03-02']
df_2 = df_2[(df_2.index < '2023-03-02 09:48') | (df_2.index >= '2023-03-02 09:49')]

df_3 = df.loc['2023-03-03']

df_8 = df.loc['2023-03-08']
df_8 = df_8[(df_8.index < '2023-03-08 09:19:10') | (df_8.index >= '2023-03-08 09:21:40')]


df_9 = df.loc['2023-03-09']
df_9.drop(df_9[df_9['CTD_Temp_SML']>6.2].index, inplace = True)

df_10 = df.loc['2023-03-10']

df_11 = df.loc['2023-03-11']

df_17 = df.loc['2023-03-17']
df_17 = df_17[df_17.index > '2023-03-17 08:03']

df_18 = df.loc['2023-03-18']
df_18 = df_18[df_18.index > '2023-03-18 07:50']

df_19 = df.loc['2023-03-19']
df_19 = df_19[(df_19.index < '2023-03-08 10:15:30') | (df_19.index >= '2023-03-19 10:16:20')]

df_20 = df.loc['2023-03-20']


all_df = [df_2, df_3, df_8, df_9, df_10, df_11, df_17, df_18, df_19, df_20]

In [4]:
# ALL MISSION: plot all CTD Temps
for df in all_df: 
# check RBR temps
    filtered_columns = [col for col in df.columns if col.startswith('CTD_Temp')]


    # Create the plotly figure
    fig = go.Figure()

    for i, col in enumerate(filtered_columns):
        fig.add_trace(go.Scatter(
            x=df.index,
            y=df[col],
            mode='markers',
            marker = {'size' : 4},
            name=f'{col}'
    ))



    fig.add_trace(go.Scatter(
        x=df.index,
        y=df['Campbell_Air_Temperature'],
        mode='lines',
        #mode=mode,
        marker = {'size' : 4,
                'color' : 'orange'},
        name='Campbell_Air'
    ))

    # fig.add_trace(go.Scatter(
    #     x=df.index,
    #     y=df['Campbell_Airtemp_smoothed'],
    #     mode='lines',
    #     #mode=mode,
    #     marker = dict(size=2),
    #     name='Campbell_Air_smoothed'
    # ))

    # Customize the layout
    fig.update_layout(
        title=f'Halobates Temperature CTD, Campbell {str(df['Date'][0])}',
        xaxis_title='Time',
        yaxis_title='Temperature',
        template='plotly_white',
        width=800,  # Set the width of the figure
        height=300,  # Set the height of the figure

        margin=dict(l=40, r=40, t=40, b=40)  # Customize margins
    )


    fig.show()

In [4]:
df = df_2
'''
WINDOWSIZES:
df_2 : 400
df_3: split? first part lower than second part
df_8: 260
df_17: 220
'''
windowsize = 6
df['CTD_Temp_100_smoothed'] = df['CTD_Temperature_100cm_[°C]'].rolling(window = windowsize, center=True).mean()

df['CTD_Temp_SML_smoothed'] = df['CTD_Temp_SML'].rolling(window = windowsize, center = True).mean()

fig = go.Figure()


fig.add_trace(go.Scatter(
    x = df.index,
    y = df['CTD_Temp_SML'], 
    mode = 'markers', 
    marker = {'color' : 'orange',
              'size' : 2},
    name = 'SML'
))

fig.add_trace(go.Scatter(
    x = df.index,
    y = df['CTD_Temperature_100cm_[°C]'], 
    mode = 'markers', 
    marker = {'color' : 'red',
              'size' : 2},
    name = '100cm'
))

fig.add_trace(go.Scatter(
    x = df.index,
    y = df['CTD_Temp_SML_smoothed'], 
    mode = 'lines', 
    marker = {'color' : 'deeppink',
              'size' : 6},
    name = 'SML_smoothed'
))

fig.add_trace(go.Scatter(
    x = df.index,
    y = df['CTD_Temp_100_smoothed'], 
    mode = 'lines', 
    marker = {'color' : 'blue', 
              'size' : 6},
    name = '100cm smoothed'
))


fig.update_layout(
    title = 'residual noise',
    xaxis_title = 'time',
    yaxis_title = 'Temperature',
    template = 'plotly_white',

)


